In [2]:
def generate_star():
    train = []
    test = []
    for i in range(1, 5):
        for j in range(1, 5):
            if i==j:
                test.append((i, 5, 5+j))
            else:
                train.append((i, 5, 5+j))
    return train, test

train, test = generate_star()

def add_new_automata(train, test):
    new_train = train.copy()
    new_test = test.copy()
    for i in range(9, 72, 9):
        for sample in train:
            a, b, c = sample
            new_train.append((a+i, b+i, c+i))
        for sample in test:
            a, b, c = sample
            new_test.append((a+i, b+i, c+i))
    return new_train, new_test

train, test = add_new_automata(train, test)

In [3]:
len(test)

32

In [4]:
def get_paths(train):
    train_paths = []
    for i in train:
        train_paths.append(i)
        tup1 = (i[0], i[1])
        train_paths.append(tup1)
        tup2 = (i[1], i[2])
        train_paths.append(tup2)
    return train_paths

train_paths = get_paths(train)
print(len(train_paths))
train_paths = list(sorted(set(get_paths(train))))

288


In [5]:
# test_paths = get_paths(test)

In [8]:
test

[(1, 5, 6),
 (2, 5, 7),
 (3, 5, 8),
 (4, 5, 9),
 (10, 14, 15),
 (11, 14, 16),
 (12, 14, 17),
 (13, 14, 18),
 (19, 23, 24),
 (20, 23, 25),
 (21, 23, 26),
 (22, 23, 27),
 (28, 32, 33),
 (29, 32, 34),
 (30, 32, 35),
 (31, 32, 36),
 (37, 41, 42),
 (38, 41, 43),
 (39, 41, 44),
 (40, 41, 45),
 (46, 50, 51),
 (47, 50, 52),
 (48, 50, 53),
 (49, 50, 54),
 (55, 59, 60),
 (56, 59, 61),
 (57, 59, 62),
 (58, 59, 63),
 (64, 68, 69),
 (65, 68, 70),
 (66, 68, 71),
 (67, 68, 72)]

In [50]:
# nejdříve vygenerovat 3 možné cesty pro každou hvězdu z trainu
# (1,5,6) - (1,5), (5,6)
# 1-5 nesmí být distractor
# samplovat dvojice a trojice (50/50) z jiných hvězd jako distractory
# když bude chybět, dát random distractor z jiných hvězd
# potom permutace
# poslední pozice = cílový automat (5 nebo 6)

import itertools
import random
from collections import defaultdict

automata_to_exluded_automata = {i: range(1 + 9*i, 6 + 9*i) for i in range(8)}
star_to_excluded_automata = {i: range(1 + 9*i, 10 + 9*i) for i in range(8)}

def get_distractors(paths, n, train=False):
    combinations = defaultdict(list)
    all_elements = set(element for path in paths for element in path)
    for i, path in enumerate(paths):
        if train:
            group = i // 20
        else:
            group = i // 4

        excluded = set(automata_to_exluded_automata[group])
        candidates = [c for c in paths if not set(c).intersection(excluded)]
        current_star_automata = set(star_to_excluded_automata[group])
        while len(combinations[path]) < n and candidates:
            candidate = random.choice(candidates)
            sample_size = min(len(candidate), random.randint(2, 3))
            inner_list = random.sample(candidate, sample_size)
            
            while len(path) + len(inner_list) < 20:
                available = all_elements - set(path) - set(inner_list) - excluded - current_star_automata
                inner_list.append(random.choice(list(available)))
            
            combinations[path].append(inner_list)
            # candidates.remove(candidate)
            # excluded.update(candidate)

    return combinations

In [51]:
combinations_train = get_distractors(train, 100, True)
combinations_test = get_distractors(test, 1, False)


In [52]:
combinations_train

defaultdict(list,
            {(1,
              5,
              7): [[41,
               44,
               59,
               72,
               22,
               52,
               29,
               33,
               45,
               35,
               19,
               24,
               63,
               39,
               66,
               61,
               42], [59,
               63,
               18,
               38,
               42,
               28,
               27,
               52,
               60,
               15,
               61,
               44,
               37,
               65,
               26,
               31,
               16], [14,
               13,
               56,
               47,
               62,
               46,
               11,
               51,
               38,
               15,
               69,
               20,
               36,
               22,
               33,
               17,
               55],

In [53]:
combinations_test

defaultdict(list,
            {(1,
              5,
              6): [[50,
               47,
               10,
               15,
               35,
               31,
               12,
               62,
               52,
               34,
               30,
               59,
               41,
               33,
               23,
               46,
               36]],
             (2,
              5,
              7): [[59,
               60,
               55,
               15,
               33,
               18,
               68,
               56,
               23,
               72,
               38,
               50,
               40,
               53,
               31,
               61,
               44]],
             (3,
              5,
              8): [[53,
               48,
               50,
               33,
               20,
               52,
               14,
               56,
               26,
               68,
               18,
      

In [54]:
# napárovat train a test podle ID
# {id: (train), (test)}

# nejdříve vygenerovat 3 možné cesty pro každou hvězdu z trainu
# (1,5,6) - (1,5), (5,6)
# 1-5 nesmí být distractor
# samplovat dvojice a trojice (50/50) z jiných hvězd jako distractory
# když bude chybět, dát random distractor z jiných hvězd
# potom permutace
# poslední pozice = cílový automat (5 nebo 6)

In [55]:
import random
import itertools

def generate_train(combinations):
    l_of_d = []
    for path, inner_lists in combinations.items():
        for lst in inner_lists:
            # Generate a few random permutations instead of all possible permutations
            num_permutations = min(10, len(lst))  # Adjust this number as needed
            for _ in range(num_permutations):
                new_lst = lst.copy()
                random.shuffle(new_lst)
                
                new_lst += path[:-1]
                random.shuffle(new_lst)
                new_lst.append(path[-1])
                
                d = {"input": new_lst, "orig_idx": new_lst.index(path[0]), "target_idx": new_lst.index(path[0]) + 73}
                l_of_d.append(d)

    return l_of_d

In [56]:
def generate_test(combinations):
    l_of_d = []
    for path, inner_lists in combinations.items():
        for lst in inner_lists:
            new_lst = list(lst)
            new_lst += path[:-1]
            random.shuffle(new_lst)
            new_lst.append(path[-1])
            d = {"input": new_lst, "orig_idx": new_lst.index(path[0]), "target_idx": new_lst.index(path[0]) + 73}
            l_of_d.append(d)

    return l_of_d

In [57]:
result_test = generate_test(combinations_test)
result_train = generate_train(combinations_train)

In [58]:
len(result_train)

96000

In [79]:
data = {"train": result_train, "test": result_test}
import pickle
with open ("new_data.pkl", "wb") as f:
    pickle.dump(data, f)

In [60]:
len(data["train"])

96000

In [61]:
len(data["test"])

32

In [62]:
data["test"]

[{'input': [47,
   46,
   52,
   50,
   23,
   36,
   33,
   12,
   59,
   35,
   41,
   15,
   34,
   1,
   5,
   62,
   30,
   31,
   10,
   6],
  'orig_idx': 13,
  'target_idx': 86},
 {'input': [50,
   72,
   5,
   55,
   44,
   38,
   53,
   59,
   31,
   61,
   56,
   18,
   40,
   2,
   68,
   23,
   33,
   15,
   60,
   7],
  'orig_idx': 13,
  'target_idx': 86},
 {'input': [68,
   5,
   48,
   56,
   18,
   26,
   52,
   3,
   20,
   37,
   69,
   53,
   34,
   27,
   40,
   50,
   14,
   60,
   33,
   8],
  'orig_idx': 7,
  'target_idx': 80},
 {'input': [38,
   68,
   64,
   31,
   12,
   5,
   15,
   14,
   63,
   52,
   47,
   60,
   4,
   16,
   35,
   67,
   61,
   51,
   18,
   9],
  'orig_idx': 12,
  'target_idx': 85},
 {'input': [50,
   61,
   68,
   6,
   21,
   69,
   46,
   43,
   29,
   10,
   42,
   39,
   8,
   41,
   53,
   37,
   1,
   14,
   67,
   15],
  'orig_idx': 9,
  'target_idx': 82},
 {'input': [14,
   47,
   37,
   19,
   23,
   67,
   71,
   2,
   42,
 

In [77]:
my_s = set()
for i in data["train"]:
    for k, v in i.items():
        if k == "target_idx":
            my_s.add(v)

In [78]:
my_s  # vocab size = 92

{73, 74, 75, 76, 77, 78, 79, 80, 81, 82, 83, 84, 85, 86, 87, 88, 89, 90, 91}